<a href="https://colab.research.google.com/github/aaliashraf/New_York_City_Business_Analysis/blob/master/DB_Projects.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
import math
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json 
import requests 
from pandas.io.json import json_normalize
print('Done')

Done


In [ ]:
!wget -q -O NY_data.json https://cocl.us/new_york_dataset
print("Done...")

Done...


In [ ]:
with open ('NY_data.json') as json_data:
    NY_data=json.load(json_data)
NY_data

{'bbox': [-74.2492599487305,
  40.5033187866211,
  -73.7061614990234,
  40.9105606079102],
 'crs': {'properties': {'name': 'urn:ogc:def:crs:EPSG::4326'}, 'type': 'name'},
 'features': [{'geometry': {'coordinates': [-73.84720052054902,
     40.89470517661],
    'type': 'Point'},
   'geometry_name': 'geom',
   'id': 'nyu_2451_34572.1',
   'properties': {'annoangle': 0.0,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661],
    'borough': 'Bronx',
    'name': 'Wakefield',
    'stacked': 1},
   'type': 'Feature'},
  {'geometry': {'coordinates': [-73.82993910812398, 40.87429419303012],
    'type': 'Point'},
   'geometry_name': 'geom',
   'id': 'nyu_2451_34572.2',
   'properties': {'annoangle': 0.0,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.874294193

In [ ]:
neighbor_data=NY_data['features']
neighbor_data

[{'geometry': {'coordinates': [-73.84720052054902, 40.89470517661],
   'type': 'Point'},
  'geometry_name': 'geom',
  'id': 'nyu_2451_34572.1',
  'properties': {'annoangle': 0.0,
   'annoline1': 'Wakefield',
   'annoline2': None,
   'annoline3': None,
   'bbox': [-73.84720052054902,
    40.89470517661,
    -73.84720052054902,
    40.89470517661],
   'borough': 'Bronx',
   'name': 'Wakefield',
   'stacked': 1},
  'type': 'Feature'},
 {'geometry': {'coordinates': [-73.82993910812398, 40.87429419303012],
   'type': 'Point'},
  'geometry_name': 'geom',
  'id': 'nyu_2451_34572.2',
  'properties': {'annoangle': 0.0,
   'annoline1': 'Co-op',
   'annoline2': 'City',
   'annoline3': None,
   'bbox': [-73.82993910812398,
    40.87429419303012,
    -73.82993910812398,
    40.87429419303012],
   'borough': 'Bronx',
   'name': 'Co-op City',
   'stacked': 2},
  'type': 'Feature'},
 {'geometry': {'coordinates': [-73.82780644716412, 40.887555677350775],
   'type': 'Point'},
  'geometry_name': 'geom',


In [ ]:
column_name=['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
neighborhood=pd.DataFrame(columns=column_name)


for data in neighbor_data:
    borough=data['properties']['borough']
    name=data['properties']['name']
    lat_lon=data['geometry']['coordinates']
    longitude=lat_lon[0]
    latitude=lat_lon[1]
    neighborhood=neighborhood.append({'Borough':borough,
                                     'Neighborhood':name,
                                     'Latitude':latitude,
                                     'Longitude':longitude},ignore_index=True)
neighborhood.head(5)

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [ ]:
neighborhood.loc[0,'Neighborhood']

'Wakefield'

In [ ]:
CLIENT_ID='R2R05S3T5J04JUU4YNXM5KEELQIH23P3X4131WIP2FPSXWBO'
CLIENT_SECRET='KNYYIHC0W5JVHAOCVSACG23I0OOTATQEHGRG3JE0NWT1YSQ3'
VERSION='20180604'
LIMIT=30
radius=500
print("the credentials:")
print("Client_id :"+CLIENT_ID)
print("CLIENT_SECRET :"+CLIENT_SECRET)

the credentials:
Client_id :R2R05S3T5J04JUU4YNXM5KEELQIH23P3X4131WIP2FPSXWBO
CLIENT_SECRET :KNYYIHC0W5JVHAOCVSACG23I0OOTATQEHGRG3JE0NWT1YSQ3


In [ ]:
neighborhood_lat=neighborhood.loc[0,'Latitude']
neighborhood_lng=neighborhood.loc[0,'Longitude']


In [ ]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
      
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            neighborhood_lat, 
            neighborhood_lng, 
            radius, 
            LIMIT)
            
       
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
       
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [ ]:
nyc_venues= getNearbyVenues(names=neighborhood['Neighborhood'],
                                   latitudes=neighborhood['Latitude'],
                                   longitudes=neighborhood['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [ ]:
nyc_venues

Neighborhood  Neighborhood Latitude  \
0                     Wakefield              40.894705   
1                     Wakefield              40.894705   
2                     Wakefield              40.894705   
3                     Wakefield              40.894705   
4                     Wakefield              40.894705   
5                     Wakefield              40.894705   
6                     Wakefield              40.894705   
7                     Wakefield              40.894705   
8                     Wakefield              40.894705   
9                     Wakefield              40.894705   
10                    Wakefield              40.894705   
11                   Co-op City              40.874294   
12                   Co-op City              40.874294   
13                   Co-op City              40.874294   
14                   Co-op City              40.874294   
15                   Co-op City              40.874294   
16                   Co-op City              40.874294   
17                   Co-op City              40.874294   
18                   Co-op City              40.874294   
19                   Co-op City              40.874294   
20                   Co-op City              40.874294   
21                   Co-op City              40.874294   
22                  Eastchester              40.887556   
23                  Eastchester              40.887556   
24                  Eastchester              40.887556   
25                  Eastchester              40.887556   
26                  Eastchester              40.887556   
27                  Eastchester              40.887556   
28                  Eastchester              40.887556   
29                  Eastchester              40.887556   
30                  Eastchester              40.887556   
31                  Eastchester              40.887556   
32                  Eastchester              40.887556   
33                    Fieldston              40.895437   
34                    Fieldston              40.895437   
35                    Fieldston              40.895437   
36                    Fieldston              40.895437   
37                    Fieldston              40.895437   
38                    Fieldston              40.895437   
39                    Fieldston              40.895437   
40                    Fieldston              40.895437   
41                    Fieldston              40.895437   
42                    Fieldston              40.895437   
43                    Fieldston              40.895437   
44                    Riverdale              40.890834   
45                    Riverdale              40.890834   
46                    Riverdale              40.890834   
47                    Riverdale              40.890834   
48                    Riverdale              40.890834   
49                    Riverdale              40.890834   
50                    Riverdale              40.890834   
51                    Riverdale              40.890834   
52                    Riverdale              40.890834   
53                    Riverdale              40.890834   
54                    Riverdale              40.890834   
55                  Kingsbridge              40.881687   
56                  Kingsbridge              40.881687   
57                  Kingsbridge              40.881687   
58                  Kingsbridge              40.881687   
59                  Kingsbridge              40.881687   
60                  Kingsbridge              40.881687   
61                  Kingsbridge              40.881687   
62                  Kingsbridge              40.881687   
63                  Kingsbridge              40.881687   
64                  Kingsbridge              40.881687   
65                  Kingsbridge              40.881687   
66                  Marble Hill              40.876551   
67                  Marble Hill              40.876551   
68               

In [ ]:
center_region=nyc_venues.loc[nyc_venues['Neighborhood']=='Madison']

cen_name=center_region['Neighborhood'].unique()
center_lat=center_region['Neighborhood Latitude'].unique()
center_lng=center_region['Neighborhood Longitude'].unique()
print("Name{},Lat{},Lng{}".format(cen_name,center_lat,center_lng))

Name['Madison'],Lat[40.6093777],Lng[-73.94841515]


In [ ]:

re_lat=nyc_venues['Neighborhood Longitude'].reset_index(drop=True)
re_lng=nyc_venues['Neighborhood Longitude'].reset_index(drop=True)
re_lat
print(re_lng)

0      -73.847201
1      -73.847201
2      -73.847201
3      -73.847201
4      -73.847201
5      -73.847201
6      -73.847201
7      -73.847201
8      -73.847201
9      -73.847201
10     -73.847201
11     -73.829939
12     -73.829939
13     -73.829939
14     -73.829939
15     -73.829939
16     -73.829939
17     -73.829939
18     -73.829939
19     -73.829939
20     -73.829939
21     -73.829939
22     -73.827806
23     -73.827806
24     -73.827806
25     -73.827806
26     -73.827806
27     -73.827806
28     -73.827806
29     -73.827806
30     -73.827806
31     -73.827806
32     -73.827806
33     -73.905643
34     -73.905643
35     -73.905643
36     -73.905643
37     -73.905643
38     -73.905643
39     -73.905643
40     -73.905643
41     -73.905643
42     -73.905643
43     -73.905643
44     -73.912585
45     -73.912585
46     -73.912585
47     -73.912585
48     -73.912585
49     -73.912585
50     -73.912585
51     -73.912585
52     -73.912585
53     -73.912585
54     -73.912585
55     -73

In [ ]:
from math import radians, cos, sin, asin, sqrt 
def distance(lat1, lat2, lon1, lon2): 
      
    # The math module contains a function named 
    # radians which converts from degrees to radians. 
    lon1 = radians(lon1) 
    lon2 = radians(lon2) 
    lat1 = radians(lat1) 
    lat2 = radians(lat2) 
       
    # Haversine formula  
    dlon = lon2 - lon1  
    dlat = lat2 - lat1 
    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
  
    c = 2 * asin(sqrt(a))  
     
    # Radius of earth in kilometers. Use 3956 for miles 
    r = 6371
       
    # calculate the result 
    return(c * r) 
      
      
# # driver code  
# lat1 = 53.32055555555556
# lat2 = 53.31861111111111
# lon1 = -1.7297222222222221
# lon2 =  -1.6997222222222223
# print(distance(lat1, lat2, lon1, lon2), "K.M") 


In [ ]:
# df1=pd.DataFrame()
# df1['Center Latitude']=center_lat
# df1['Center Longitude']=center_lng
# df1
df['Center Latitude']=df.apply(lambda x:center_lat,axis=1)
df['Center Longitude']=df.apply(lambda x:center_lng,axis=1)
df['Center Latitude'] = df['Center Latitude'].str.get(0)
df['Center Longitude'] = df['Center Longitude'].str.get(0)
df

Center Latitude  Neighborhood Latitude  Center Longitude  \
Center Latitude                                                             
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.894705        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.874294        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.887556        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.895437        -73.948415   
40.609378              40.609378              40.890834        -73.948415   
40.609378              40.609378              40.890834        -73.948415   
40.609378              40.609378              40.890834        -73.948415   
40.609378              40.609378              40.890834        -73.948415   
40.609378              40.609378              40.890834        -73.948415   
40.609378              40.609378              40.890834        -73.948415   
40.609378    

In [ ]:
df=df[['Center Latitude','Neighborhood Latitude','Center Longitude','Neighborhood Longitude']]
df.reset_index(drop=True, inplace=True)
df

Center Latitude  Neighborhood Latitude  Center Longitude  \
0           40.609378              40.894705        -73.948415   
1           40.609378              40.894705        -73.948415   
2           40.609378              40.894705        -73.948415   
3           40.609378              40.894705        -73.948415   
4           40.609378              40.894705        -73.948415   
5           40.609378              40.894705        -73.948415   
6           40.609378              40.894705        -73.948415   
7           40.609378              40.894705        -73.948415   
8           40.609378              40.894705        -73.948415   
9           40.609378              40.894705        -73.948415   
10          40.609378              40.894705        -73.948415   
11          40.609378              40.874294        -73.948415   
12          40.609378              40.874294        -73.948415   
13          40.609378              40.874294        -73.948415   
14          40.609378              40.874294        -73.948415   
15          40.609378              40.874294        -73.948415   
16          40.609378              40.874294        -73.948415   
17          40.609378              40.874294        -73.948415   
18          40.609378              40.874294        -73.948415   
19          40.609378              40.874294        -73.948415   
20          40.609378              40.874294        -73.948415   
21          40.609378              40.874294        -73.948415   
22          40.609378              40.887556        -73.948415   
23          40.609378              40.887556        -73.948415   
24          40.609378              40.887556        -73.948415   
25          40.609378              40.887556        -73.948415   
26          40.609378              40.887556        -73.948415   
27          40.609378              40.887556        -73.948415   
28          40.609378              40.887556        -73.948415   
29          40.609378              40.887556        -73.948415   
30          40.609378              40.887556        -73.948415   
31          40.609378              40.887556        -73.948415   
32          40.609378              40.887556        -73.948415   
33          40.609378              40.895437        -73.948415   
34          40.609378              40.895437        -73.948415   
35          40.609378              40.895437        -73.948415   
36          40.609378              40.895437        -73.948415   
37          40.609378              40.895437        -73.948415   
38          40.609378              40.895437        -73.948415   
39          40.609378              40.895437        -73.948415   
40          40.609378              40.895437        -73.948415   
41          40.609378              40.895437        -73.948415   
42          40.609378              40.895437        -73.948415   
43          40.609378              40.895437        -73.948415   
44          40.609378              40.890834        -73.948415   
45          40.609378              40.890834        -73.948415   
46          40.609378              40.890834        -73.948415   
47          40.609378              40.890834        -73.948415   
48          40.609378              40.890834        -73.948415   
49          40.609378              40.890834        -73.948415   
50          40.609378              40.890834        -73.948415   
51          40.609378              40.890834        -73.948415   
52          40.609378              40.890834        -73.948415   
53          40.609378              40.890834        -73.948415   
54          40.609378              40.890834        -73.948415   
55          40.609378              40.881687        -73.948415   
56          40.609378              40.881687        -73.948415   
57          40.609378              40.881687        -73.948415   
58          40.609378              40.881687        -73.948415   
59          40.609378              40.881687  

In [ ]:

df['formula=']=df.apply(lambda x:distance(*x),axis=1)


df

Center Latitude  Neighborhood Latitude  Center Longitude  \
0           40.609378              40.894705        -73.948415   
1           40.609378              40.894705        -73.948415   
2           40.609378              40.894705        -73.948415   
3           40.609378              40.894705        -73.948415   
4           40.609378              40.894705        -73.948415   
5           40.609378              40.894705        -73.948415   
6           40.609378              40.894705        -73.948415   
7           40.609378              40.894705        -73.948415   
8           40.609378              40.894705        -73.948415   
9           40.609378              40.894705        -73.948415   
10          40.609378              40.894705        -73.948415   
11          40.609378              40.874294        -73.948415   
12          40.609378              40.874294        -73.948415   
13          40.609378              40.874294        -73.948415   
14          40.609378              40.874294        -73.948415   
15          40.609378              40.874294        -73.948415   
16          40.609378              40.874294        -73.948415   
17          40.609378              40.874294        -73.948415   
18          40.609378              40.874294        -73.948415   
19          40.609378              40.874294        -73.948415   
20          40.609378              40.874294        -73.948415   
21          40.609378              40.874294        -73.948415   
22          40.609378              40.887556        -73.948415   
23          40.609378              40.887556        -73.948415   
24          40.609378              40.887556        -73.948415   
25          40.609378              40.887556        -73.948415   
26          40.609378              40.887556        -73.948415   
27          40.609378              40.887556        -73.948415   
28          40.609378              40.887556        -73.948415   
29          40.609378              40.887556        -73.948415   
30          40.609378              40.887556        -73.948415   
31          40.609378              40.887556        -73.948415   
32          40.609378              40.887556        -73.948415   
33          40.609378              40.895437        -73.948415   
34          40.609378              40.895437        -73.948415   
35          40.609378              40.895437        -73.948415   
36          40.609378              40.895437        -73.948415   
37          40.609378              40.895437        -73.948415   
38          40.609378              40.895437        -73.948415   
39          40.609378              40.895437        -73.948415   
40          40.609378              40.895437        -73.948415   
41          40.609378              40.895437        -73.948415   
42          40.609378              40.895437        -73.948415   
43          40.609378              40.895437        -73.948415   
44          40.609378              40.890834        -73.948415   
45          40.609378              40.890834        -73.948415   
46          40.609378              40.890834        -73.948415   
47          40.609378              40.890834        -73.948415   
48          40.609378              40.890834        -73.948415   
49          40.609378              40.890834        -73.948415   
50          40.609378              40.890834        -73.948415   
51          40.609378              40.890834        -73.948415   
52          40.609378              40.890834        -73.948415   
53          40.609378              40.890834        -73.948415   
54          40.609378              40.890834        -73.948415   
55          40.609378              40.881687        -73.948415   
56          40.609378              40.881687        -73.948415   
57          40.609378              40.881687        -73.948415   
58          40.609378              40.881687        -73.948415   
59          40.609378              40.881687  

In [ ]:
df.to_csv(r'DataSet New.csv')